In [1]:
cd Galvanize/Work_Done/projects/Capstone_Projects/IMP\ reserve\ materials

/Users/alex/Galvanize/Work_Done/projects/Capstone_Projects/IMP reserve materials


In [2]:
import os
import re

import pandas as pd

In [3]:
data_directory = os.path.join('data','rawASAM.csv')

df = pd.read_csv(data_directory)
df.head(1)

reference        date                 position navArea  subreg  \
0   2019-73  2019-09-30  1°02'42"N \n103°39'00"E      XI      71   

            hostility        victim  \
0  Five Armed robbers  Bulk Carrier   

                                         description  Unnamed: 8  
0  , SINGAPORE STRAITS. DECK CREW ON ROUTINE ROUN...         NaN

In [4]:
# df.drop(['Unnamed: 8'], axis=1, inplace=True)

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7843 entries, 0 to 7842
Data columns (total 9 columns):
reference      7843 non-null object
date           7843 non-null object
position       7843 non-null object
navArea        7840 non-null object
subreg         7843 non-null int64
hostility      7833 non-null object
victim         7829 non-null object
description    7843 non-null object
Unnamed: 8     0 non-null float64
dtypes: float64(1), int64(1), object(7)
memory usage: 551.6+ KB


### Split postion into Lat/Lon in prep for conversion to decimal degrees

In [6]:
df = df.join(df['position'].str.split(expand=True)).rename(columns={0:'Latitude', 1:'Longitude'})
df.drop('position', axis=1, inplace=True)

In [7]:
df.head(1)

reference        date navArea  subreg           hostility        victim  \
0   2019-73  2019-09-30      XI      71  Five Armed robbers  Bulk Carrier   

                                         description  Unnamed: 8   Latitude  \
0  , SINGAPORE STRAITS. DECK CREW ON ROUTINE ROUN...         NaN  1°02'42"N   

     Longitude  
0  103°39'00"E

In [8]:
def dms2dd(s):
    # example: s = """0°51'56.29"S"""
    degrees, minutes, seconds, direction = re.split('[°\'"]+', s)
    dd = float(degrees) + float(minutes)/60 + float(seconds)/(60*60);
    if direction in ('S','W'):
        dd*= -1
    return dd

In [9]:
df['Latitude'] = df['Latitude'].apply(dms2dd).round(6)
df['Longitude'] = df['Longitude'].apply(dms2dd).round(6)
df.head(1)

reference        date navArea  subreg           hostility        victim  \
0   2019-73  2019-09-30      XI      71  Five Armed robbers  Bulk Carrier   

                                         description  Unnamed: 8  Latitude  \
0  , SINGAPORE STRAITS. DECK CREW ON ROUTINE ROUN...         NaN     1.045   

   Longitude  
0     103.65

### Under 'hostility' - how many different terms are there? 327

In [10]:
df['hostility'].value_counts()

PIRATES                4350
Robbers                 834
Pirates                 612
SUSPICIOUS APPROACH     274
ROBBERS                 270
                       ... 
Roobbers                  1
suspicious vessel         1
YACHT                     1
FOUR BOATS                1
RIVAL GANG                1
Name: hostility, Length: 327, dtype: int64

In [11]:
df['hostility'].nunique()

327

### Under 'victim' - how many different terms are there? 1224

In [12]:
df['victim'].nunique()

1224

In [13]:
df['victim'].value_counts()

MERCHANT VESSEL      2639
BULK CARRIER          401
TANKER                400
CONTAINER SHIP        258
Tanker                250
                     ... 
Passenger boat          1
BARGE/TUG BOAT          1
ASPIDOFOROS             1
RO-RO SHIP              1
M/V TRICOLOR SONG       1
Name: victim, Length: 1224, dtype: int64

### Convert datetime to just the year for a slider

In [14]:
df['date2'] = pd.to_datetime(df['date'], format='%Y/%m/%d')
df.head(1)

reference        date navArea  subreg           hostility        victim  \
0   2019-73  2019-09-30      XI      71  Five Armed robbers  Bulk Carrier   

                                         description  Unnamed: 8  Latitude  \
0  , SINGAPORE STRAITS. DECK CREW ON ROUTINE ROUN...         NaN     1.045   

   Longitude      date2  
0     103.65 2019-09-30

In [15]:
df['year'] = pd.DatetimeIndex(df['date2']).year
df["date"] = pd.to_datetime(df["date2"])

df = df[['reference', 'Latitude', 'Longitude', 'date', 'year', 'description', 'hostility', 'victim', 'navArea', 'subreg' ]]

# sanity check
df.head()

reference  Latitude   Longitude       date  year  \
0   2019-73  1.045000  103.650000 2019-09-30  2019   
1   2019-72  5.325000  119.728333 2019-09-28  2019   
2   2019-75  6.283333    3.233333 2019-09-23  2019   
3   2019-74  5.464764  119.121597 2019-09-23  2019   
4   2019-76  9.416667  -13.733333 2019-09-16  2019   

                                         description  \
0  , SINGAPORE STRAITS. DECK CREW ON ROUTINE ROUN...   
1  AROUND 12NM NW OF TAWI-TAWI ISLAND, PHILIPPINE...   
2  On September 23rd a duty watchman on board a t...   
3  TWO FISHING BOATS SAILED TOWARDS TAMBISAN FOR ...   
4  On September 16th four robbers armed with a gu...   

                    hostility               victim navArea  subreg  
0          Five Armed robbers         Bulk Carrier      XI      71  
1        Two High-speed boats         Bulk Carrier      XI      92  
2                         NaN                  NaN      II      57  
3  Seven people in Pump Boats  two fishing vessels      XI      72  
4          Four armed robbers               Tanker      II      51

### Right, the NaNs would mess things up. Let's convert them to something that can be parsed later

In [18]:
df.fillna("No information", inplace=True)
df.isnull().sum().sum()
df.head(5)

reference  Latitude   Longitude       date  year  \
0   2019-73  1.045000  103.650000 2019-09-30  2019   
1   2019-72  5.325000  119.728333 2019-09-28  2019   
2   2019-75  6.283333    3.233333 2019-09-23  2019   
3   2019-74  5.464764  119.121597 2019-09-23  2019   
4   2019-76  9.416667  -13.733333 2019-09-16  2019   

                                         description  \
0  , SINGAPORE STRAITS. DECK CREW ON ROUTINE ROUN...   
1  AROUND 12NM NW OF TAWI-TAWI ISLAND, PHILIPPINE...   
2  On September 23rd a duty watchman on board a t...   
3  TWO FISHING BOATS SAILED TOWARDS TAMBISAN FOR ...   
4  On September 16th four robbers armed with a gu...   

                    hostility               victim navArea  subreg  
0          Five Armed robbers         Bulk Carrier      XI      71  
1        Two High-speed boats         Bulk Carrier      XI      92  
2              No information       No information      II      57  
3  Seven people in Pump Boats  two fishing vessels      XI      72  
4          Four armed robbers               Tanker      II      51

### I'd like this to eventually be a live demo, not that there are all that many attacks per year. But, since it's on the web, this is usually sent as JSON

In [17]:
df.to_json('..data/mungedASAM.json', date_format='iso', orient='records')

'[{"reference":"2019-73","Latitude":1.045,"Longitude":103.65,"date":1569801600000,"year":2019,"description":", SINGAPORE STRAITS. DECK CREW ON ROUTINE ROUNDS ONBOARD THE BULK CARRIRE UNDERWAY IN THE SINGAPORE TSS SPOTTED FIVE ARMED ROBBERS ON THE AFT DECK. ALARM RAISED, SSAS ACTIVATED AND PA ANNOUNCEMENT MADE RESULTING IN THE ROBBERS ESCAPING WITHOUT STEALING ANYTHING. INCIDENT REPORTED TO SINGAPORE VTIS. AFTER ALMOST ONE HOUR AND IN SINGAPORE WATERS, A SINGAPORE POLICE COAST GUARD BOAT INTERCEPTED AND ESCORTED THE SHIP TO SINGAPORE, WHERE THEY BOARDED AND SEARCHED THE SHIP TO ENSURE THAT THE ROBBERS HAD LEFT.","hostility":"Five Armed robbers","victim":"Bulk Carrier","navArea":"XI","subreg":71},{"reference":"2019-72","Latitude":5.325,"Longitude":119.728333,"date":1569628800000,"year":2019,"description":"AROUND 12NM NW OF TAWI-TAWI ISLAND, PHILIPPINES. TWO SUSPICIOUS HIGH-SPEED BOATS APPROACHED A BULK CARRIER UNDERWAY. MASTER RAISED THE ALARM, CREW MUSTERED AND ACTIVATED PRESSURIZED FIR

In [25]:
pwd

'/Users/alex/Galvanize/Work_Done/projects/Capstone_Projects/IMP reserve materials'

In [27]:
ls

1962_2006_walmart_store_openings.csv
ASAM_clean_scrub copy.txt
ASAM_clean_scrub.txt
ASAM_cleaned.csv
Alex Rook Proposal 1.pdf
Analysising world piracy.ipynb
Capstone 1 lessons learned.md
Dash_map_data.py
Data_wo_Notex.csv
LeroyJenkins.txt
Modern_NLP_in_Python.ipynb
Plt_chlor_w_slider.py
Scraping3.py
Untitled.ipynb
Untitled1.ipynb
Untitled2.ipynb
Untitled3.ipynb
app2.py
chloro.py
data/
data copy.csv
data_to_use.csv
dataa.csv
datab.csv
datac.csv
earlier_data/
holding/
images/
modern-nlp-in-python-master/
modern-nlp-in-python-master.zip
notebooks/
parsing.py
parsing_w_lxml.py
piracy_html.txt
piracytab.txt
plot_topics_extraction_with_nmf_lda.ipynb
readme.md
reg2sql.py
scraping.py
src/
test code for Capstone1.ipynb
wmt.py
wmt2.py
wmt_ex.py


In [31]:
with open('data/temp.json', 'w') as f:
    f.write(df.to_json(orient='records', lines=True))

## And now to put all that into production.